In [1]:
#%%
import os, sys, re
path = []
for p in sys.path:
    if "RMG-Py" in p:
        path.append('/work/westgroup/Importer/RMG-Py/')
    else:
        path.append(p)
sys.path = path
import numpy as np
import pandas as pd
import pickle
import logging
logging.getLogger("imported_module").setLevel(logging.WARNING)
import subprocess
import yaml
logger = logging.getLogger('my-logger')
logger.propagate = False
from autotst.reaction import Reaction, TS
from autotst.species import Species, Conformer
import multiprocessing
from multiprocessing import Manager, Process

import rmgpy
from rmgpy.thermo import NASA, ThermoData, Wilhoit, NASAPolynomial
import rmgpy.constants as constants
from rmgpy.kinetics import Arrhenius, ArrheniusEP, ThirdBody, Lindemann, Troe, \
                           PDepArrhenius, MultiArrhenius, MultiPDepArrhenius, \
                           Chebyshev, KineticsData, PDepKineticsModel
from rmgpy.data.kinetics.library import KineticsLibrary
from rmgpy.data.thermo import ThermoLibrary
from rmgpy.molecule import Molecule as RMGMolecule 
from rmgpy.species import Species as RMGSpecies
from rmgpy.reaction import Reaction as RMGReaction

from autotst.data.inputoutput import InputOutput, get_possible_names
import ck2cti


RDKit WARNING: [15:56:37] Enabling RDKit 2019.09.2 jupyter extensions


# Getting the ` ck2cti` parsers

In [2]:
models_directories = {
    '../models/2028-Sarathy/':'../alternatives/butanol',
    '../models/n-Heptane/':'../alternatives/heptane',
    '../models/335-Wang/':'../alternatives/methylheptane'
}

parsers = {}

for dirpath, alternate_dirpath in models_directories.items():
    species_filepath = os.path.join(dirpath,  "RMG-Py-kinetics-library", "dictionary.txt")
    species_dict = rmgpy.data.kinetics.KineticsLibrary().get_species(species_filepath)
    species_list = [sp for sp in species_dict.values()]

    with open(os.path.join(dirpath,'import.sh')) as infile:
        shellscript = infile.read()

    reactions_filename = re.search('--reactions\s+(\S+)',shellscript).group(1)
    reactions_filepath = os.path.join(dirpath,reactions_filename)

    thermo_filename = re.search('--thermo\s+(\S+)',shellscript).group(1)
    thermo_filepath = os.path.join(dirpath,thermo_filename)

    parser = ck2cti.Parser()
    surfaces = parser.convertMech(inputFile=reactions_filepath,
                                    thermoFile=thermo_filepath,
                                    transportFile=None,
                                    surfaceFile=None,
                                    phaseName='gas',
                                    outName=os.path.join(alternate_dirpath,'master.cti'),
                                    permissive=True)
    
    parsers[alternate_dirpath.split('/')[-1]] = (parser, species_dict, species_list)
    
parsers

ck2cti.py:953 warn WARNING Found reversible reaction containing a product photon:
oh*<=>oh+hv                                  1.450e+06      0.0           0.0
If the "--permissive" option was specified, this will be converted to an irreversible reaction with the photon removed.
ck2cti.py:953 warn WARNING Found reversible reaction containing a product photon:
ch*<=>ch+hv 1.860e+06 0.0 0.0
If the "--permissive" option was specified, this will be converted to an irreversible reaction with the photon removed.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "hoco" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ch3cho2h" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ch3coch2o2h" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ch3coch2o" while reading thermodynamics entry.
ck2cti.py:953 warn WARNING Found additional 

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "o2c5h10oh-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h6" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c*ccjc*c" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h5" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "l-c6h4" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c-c6h4" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h5oh" while reading thermodynamics entry.
ck2cti.py:1746 loadC

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h223" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h212" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h213" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h2m1" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h2m2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h2m3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4ohket1-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4ohket1-3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4ohket1-m" while reading thermody

Wrote CTI mechanism file to '../alternatives/butanol/master.cti'.
Mechanism contains 431 species and 2346 reactions.


ck2cti.py:953 warn WARNING Found additional declaration of species TIC4H7Q2-I
ck2cti.py:953 warn WARNING Found additional declaration of species IIC4H7Q2-T
ck2cti.py:953 warn WARNING Found additional declaration of species IIC4H7Q2-I
ck2cti.py:953 warn WARNING Found additional declaration of species CH2O2H
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "HOCO" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "CH3CHO2H" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "CH3CHCHO" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "C3H51-2V3OOH" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "C3H52-1V3OOH" while reading thermodynamics entry.
ck2cti.py:953 warn WARNING Found additional thermo entry for species C5H11O-1. If --permissive was given, the first entry is used.
ck

...

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket11-14-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket11-15-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-8-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-9-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-10-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-11-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-13-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-14-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c19ket12-

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket4-6-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket4-7-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket4-8-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket5-3-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket5-4-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket5-6-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket5-7-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket5-8-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket5-9-2" while read

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-10-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-11-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-12-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-13-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-15-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-16-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-17-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket14-18-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket1

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc11h23coc3h6p" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc10h21coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc10h21coc3h6p" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc9h19coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc9h19coc3h6p" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc8h17coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc7h15coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc6h13coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "nc5h11coc

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic15h31cho" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic15h31co" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic16h33cho" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic16h33co" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic17h35cho" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic17h35co" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic6h13coch3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic7h15coch3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic8h17coch3" while reading therm

# Reading in all of the AutoTST results we have so far

In [3]:
reactions_to_process = {}

# Something is happening here that results in one reaction not being parsed

atst_dir = '../autotst-results/'
rmg_reactions = np.load('../find-reactions/autotst-reactions.npy')

for rmg_reaction in rmg_reactions:
    atst_reaction = Reaction(rmg_reaction = rmg_reaction)
    labeled_reaction, family = atst_reaction.get_labeled_reaction()
    
    possible_names = get_possible_names(
        [s.to_smiles() for s in labeled_reaction.reactants],
        [s.to_smiles() for s in labeled_reaction.products]
    )
    found_result = False
    reaction_dict = {'rmg_reaction':rmg_reaction, 'family':family,'atst':None}
    for possible_name in possible_names:
        kinetics_path = os.path.join(atst_dir, f'{possible_name}.kinetics')
        if os.path.exists(kinetics_path):
            io = InputOutput(reaction=atst_reaction)
            local_context = io.read_kinetics_file(kinetics_path)
            reaction_dict['atst'] = local_context['reaction'].kinetics
            found_result = True
            break
    reactions_to_process[possible_name] = reaction_dict
       

reaction.py:167 load_databases INFO Loading RMG database from '/Users/nathan/anaconda3/envs/tst_env/share/rmgdatabase'
thermo.py:900 load_libraries INFO Loading thermodynamics library from primaryThermoLibrary.py in /Users/nathan/anaconda3/envs/tst_env/share/rmgdatabase/thermo/libraries...
thermo.py:900 load_libraries INFO Loading thermodynamics library from thermo_DFT_CCSDTF12_BAC.py in /Users/nathan/anaconda3/envs/tst_env/share/rmgdatabase/thermo/libraries...
thermo.py:900 load_libraries INFO Loading thermodynamics library from CBS_QB3_1dHR.py in /Users/nathan/anaconda3/envs/tst_env/share/rmgdatabase/thermo/libraries...
thermo.py:919 load_groups INFO Loading thermodynamics group database from /Users/nathan/anaconda3/envs/tst_env/share/rmgdatabase/thermo/groups...
transport.py:294 load_groups INFO Loading transport group database from /Users/nathan/anaconda3/envs/tst_env/share/rmgdatabase/transport/groups...
statmech.py:553 load_groups INFO Loading frequencies group database from /Use

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "C=C"> + <Molecule "[H]"> <=> <Molecule "C[CH2]"> to intra_H_migration, trying different combination...
inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../autotst-results/C=C+[H]_C[CH2].kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "C=C"> + <Molecule "[H]"> <=> <Molecule "[CH]=C"> + <Molecule "[H][H]"> to 

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "C"> + <Molecule "[OH]"> <=> <Molecule "[CH3]"> + <Molecule "O"> to intra_H_migration, trying different combination...
inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../autotst-results/C+[OH]_O+[CH3].kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse di

reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH]=C=C"> + <Molecule "[H]"> <=> <Molecule "[CH]=C=[CH]"> + <Molecule "[H][H]"> to intra_H_migration, trying different combination...
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH]=C=C"> + <Molecule "[H]"> <=> <Molecule "[CH]C#C"> + <Molecule "[H][H]"> to intra_H_migration, trying different combination...
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH]=C=C"> + <Molecule "[H]"> <=> <Molecule "[CH]C#C"> + <Molecule "[H][H]"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH2]C=C"> <=> <Molecule "C=[C]C"> to H_Abstraction, trying different combination...
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH2]C=C"> <=> <Molecule "C=[C]C"> to H_Abstraction, trying different combination...
reac

inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../autotst-results/C=C=C+[H]_[CH2]C=C.kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "C#CC"> + <Molecule "[H]"> <=> <Molecule "[CH]=C=C"> + <Molecule "[H][H]"> to H_Abstraction, trying different combination...
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reac

...

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCC(C)C"> + <Molecule "CCCC(O[O])C(C)C"> <=> <Molecule "[CH2]C(C)CCCC"> + <Molecule "CCCC(OO)C(C)C"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_react

reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CC(C)CCCCCO[O]"> <=> <Molecule "[CH2]CCCCC(C)C"> + <Molecule "CC(C)CCCCCOO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCC(CCC(C)C)O[O]"> <=> <Molecule "[CH2]CCCCC(C)C"> + <Molecule "CCC(CCC(C)C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reacti

reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCCCC(O[O])C(C)C"> <=> <Molecule "CCCCC[C](C)C"> + <Molecule "CCCCC(OO)C(C)C"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCC

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCCCC(O[O])C(C)C"> <=> <Molecule "C[CH]CCCC(C)C"> + <Molecule "CCCCC(OO)C(C)C"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_re

reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCC(CCC(C)C)O[O]"> <=> <Molecule "CCC[CH]CC(C)C"> + <Molecule "CCC(CCC(C)C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCCC(CC(C)C)O[O]"> <=> <Molecule "CCC[CH]CC(C)C"> + <Molecule "CCCC(CC(C)C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reac

# Convert it to a DF

In [4]:
df = pd.DataFrame(reactions_to_process).T[['atst', 'rmg_reaction']]
df = df.dropna()
df['atst_index'] = range(len(df))
df.head()

atst  \
[CH2]+[H][H]_[CH3]+[H]   Arrhenius(A=(37.2758,'cm^3/(mol*s)'), n=3.4832...   
C+[H]_[H][H]+[CH3]       Arrhenius(A=(1136.61,'cm^3/(mol*s)'), n=3.3407...   
[OH]+[H][H]_O+[H]        Arrhenius(A=(3.08477e+06,'cm^3/(mol*s)'), n=2....   
[CH]=C+[H]_[H][H]+[C]=C  Arrhenius(A=(2.86098e+08,'cm^3/(mol*s)'), n=1....   
C=C+[H]_C[CH2]           Arrhenius(A=(7.16226e+08,'cm^3/(mol*s)'), n=1....   

                                   rmg_reaction  atst_index  
[CH2]+[H][H]_[CH3]+[H]     CH2 + H2 <=> H + CH3           0  
C+[H]_[H][H]+[CH3]         CH4 + H <=> CH3 + H2           1  
[OH]+[H][H]_O+[H]           OH + H2 <=> H + H2O           2  
[CH]=C+[H]_[H][H]+[C]=C  C2H3 + H <=> H2CC + H2           3  
C=C+[H]_C[CH2]                C2H4 + H <=> C2H5           4

In [5]:
def cti_to_rmg(cti_reaction, species_dict):
    '''
    Helper function to convert a cti reaction to an rmg reaction
    given a species dictionary
    '''
    reactants = []
    products = []
    try:
        for number, reactant in cti_reaction.reactants:
            for _ in range(number):
                reactants.append(species_dict[reactant.label])

        for number, product in cti_reaction.products:
            for _ in range(number):
                products.append(species_dict[product.label])

        return RMGReaction(reactants=reactants, products=products)
    except KeyError:
        print(f'Error trying to convert {cti_reaction}')
        return None
        


for name, (parser, species_dict, species_list) in parsers.items():
    # Creating empty sets for indexes, cti_rxns, and cti_strings
    df[f'{name}_indexes'] = np.empty((len(df), 0)).tolist()
    df[f'{name}_cti_rxn'] = None
    df[f'{name}_cti_str'] = None
    
    for i, reaction in enumerate(parser.reactions):
        # getting an rmg reaction
        rmg_reaction = cti_to_rmg(reaction, species_dict)
        
        if rmg_reaction is None:
            # Species dict isn't complete
            continue
        
        # Finding the reactions that are isomorphic
        size = df[df.rmg_reaction.map(lambda x: rmg_reaction.is_isomorphic(x))].shape[0]
        
        if size == 0:
            # No reactions matched
            continue
            
        elif size == 1:
            # We cound exactly one match
            
            # Appending the index to known indexes
            df[df.rmg_reaction.map(
                lambda x: rmg_reaction.is_isomorphic(x))]\
                [f'{name}_indexes'].map(lambda x: x.append(i))
            
            # getting the index for this reaction
            index = df[df.rmg_reaction.map(
                lambda x: rmg_reaction.is_isomorphic(x))]\
                [f'{name}_indexes'].index[0]
            
            # Setting the kinetics properly
            rmg_reaction.kinetics = df.loc[index, 'atst']
            
            # Creating the chemkin string
            try:
                chemkin_string = rmg_reaction.to_chemkin(species_list)
            except AssertionError:
                # Reversing it if need be
                # Necessary for radical addition reactions
                # we only calc them in the 2 to 1 direction
                rmg_reaction.reactants, rmg_reaction.products = rmg_reaction.products, rmg_reaction.reactants
                chemkin_string = rmg_reaction.to_chemkin(species_list)
                
            # Chemkin string to cantera string
            chemkin_string = '\n'.join([l for l in chemkin_string.splitlines() if not l.startswith('!')])
            #print(chemkin_string)
            cantera_reaction, _ = parser.readKineticsEntry(str(chemkin_string), False)
            
            # Setting it in the df
            df.loc[index, f'{name}_cti_rxn'] = cantera_reaction
            df.loc[index, f'{name}_cti_str'] = str(cantera_reaction)
            
        else:
            # why did it match two reactions???
            _ = df[df.rmg_reaction.map(lambda x: rmg_reaction.is_isomorphic(x))]
            assert False
        
df.head()

Error trying to convert nc5h11coc2h3 + h -> h2 + c5h10-1 + c2h3co
Error trying to convert nc5h11coc2h3 + oh -> h2o + c5h10-1 + c2h3co
Error trying to convert nc5h11coc2h3 + o -> oh + c5h10-1 + c2h3co
Error trying to convert nc5h11coc2h3 + ho2 -> h2o2 + c5h10-1 + c2h3co
Error trying to convert nc5h11coc2h3 + h -> h2 + nc4h9chco + c2h3
Error trying to convert nc5h11coc2h3 + oh -> h2o + nc4h9chco + c2h3
Error trying to convert nc5h11coc2h3 + o -> oh + nc4h9chco + c2h3
Error trying to convert nc5h11coc2h3 + ho2 -> h2o2 + nc4h9chco + c2h3
Error trying to convert nc6h13coc2h3 + h -> h2 + c6h12-1 + c2h3co
Error trying to convert nc6h13coc2h3 + oh -> h2o + c6h12-1 + c2h3co
Error trying to convert nc6h13coc2h3 + o -> oh + c6h12-1 + c2h3co
Error trying to convert nc6h13coc2h3 + ho2 -> h2o2 + c6h12-1 + c2h3co
Error trying to convert nc6h13coc2h3 + h -> h2 + nc5h11chco + c2h3
Error trying to convert nc6h13coc2h3 + oh -> h2o + nc5h11chco + c2h3
Error trying to convert nc6h13coc2h3 + o -> oh + nc5h1

atst  \
[CH2]+[H][H]_[CH3]+[H]   Arrhenius(A=(37.2758,'cm^3/(mol*s)'), n=3.4832...   
C+[H]_[H][H]+[CH3]       Arrhenius(A=(1136.61,'cm^3/(mol*s)'), n=3.3407...   
[OH]+[H][H]_O+[H]        Arrhenius(A=(3.08477e+06,'cm^3/(mol*s)'), n=2....   
[CH]=C+[H]_[H][H]+[C]=C  Arrhenius(A=(2.86098e+08,'cm^3/(mol*s)'), n=1....   
C=C+[H]_C[CH2]           Arrhenius(A=(7.16226e+08,'cm^3/(mol*s)'), n=1....   

                                   rmg_reaction  atst_index butanol_indexes  \
[CH2]+[H][H]_[CH3]+[H]     CH2 + H2 <=> H + CH3           0           [167]   
C+[H]_[H][H]+[CH3]         CH4 + H <=> CH3 + H2           1           [128]   
[OH]+[H][H]_O+[H]           OH + H2 <=> H + H2O           2             [2]   
[CH]=C+[H]_[H][H]+[C]=C  C2H3 + H <=> H2CC + H2           3           [337]   
C=C+[H]_C[CH2]                C2H4 + H <=> C2H5           4           [200]   

                                 butanol_cti_rxn          butanol_cti_str  \
[CH2]+[H][H]_[CH3]+[H]   ch2(s) + h2 <=> ch3 + h  ch2(s) + h2 <=> ch3 + h   
C+[H]_[H][H]+[CH3]          ch4 + h <=> ch3 + h2     ch4 + h <=> ch3 + h2   
[OH]+[H][H]_O+[H]            oh + h2 <=> h + h2o      oh + h2 <=> h + h2o   
[CH]=C+[H]_[H][H]+[C]=C   c2h3 + h <=> h2cc + h2   c2h3 + h <=> h2cc + h2   
C=C+[H]_C[CH2]                 c2h4 + h <=> c2h5        c2h4 + h <=> c2h5   

                        heptane_indexes       heptane_cti_rxn  \
[CH2]+[H][H]_[CH3]+[H]               []                  None   
C+[H]_[H][H]+[CH3]           [177, 178]  CH3 + H2 <=> CH4 + H   
[OH]+[H][H]_O+[H]                [4, 5]   H + H2O <=> OH + H2   
[CH]=C+[H]_[H][H]+[C]=C              []                  None   
C=C+[H]_C[CH2]                    [294]     C2H4 + H <=> C2H5   

                              heptane_cti_str methylheptane_indexes  \
[CH2]+[H][H]_[CH3]+[H]                   None            [233, 234]   
C+[H]_[H][H]+[CH3]       CH3 + H2 <=> CH4 + H            [177, 178]   
[OH]+[H][H]_O+[H]         H + H2O <=> OH + H2                [4, 5]   
[CH]=C+[H]_[H][H]+[C]=C                  None                    []   
C=C+[H]_C[CH2]              C2H4 + H <=> C2H5                 [294]   

                           methylheptane_cti_rxn    methylheptane_cti_str  
[CH2]+[H][H]_[CH3]+[H]   ch3 + h <=> ch2(s) + h2  ch3 + h <=> ch2(s) + h2  
C+[H]_[H][H]+[CH3]          ch3 + h2 <=> ch4 + h     ch3 + h2 <=> ch4 + h  
[OH]+[H][H]_O+[H]            h + h2o <=> oh + h2      h + h2o <=> oh + h2  
[CH]=C+[H]_[H][H]+[C]=C                     None                     None  
C=C+[H]_C[CH2]                 c2h4 + h <=> c2h5        c2h4 + h <=> c2h5

In [6]:
# Saving it for later bc this takes a while
df.to_pickle('alternatives.pkl')

# Writing all of the files

They will have the file format: `fuel_name.autotst_index.fuel_indexes.cti`.

In [13]:
for name, (parser, *_) in parsers.items():
    original_reactions = parser.reactions[:]
    
    for rxn_string in df.index:
        indexes = df.loc[rxn_string,f'{name}_indexes']
        if len(indexes) == 0:
            continue
            
        atst_index = df.loc[rxn_string, 'atst_index']
        cti_rxn = df.loc[rxn_string, f'{name}_cti_rxn']

        #modified_reactions = original_reactions[:]
        modified_reactions = []
        for i, original_reaction in enumerate(original_reactions):
            if i in indexes:
                print(i, original_reaction)
                continue
            modified_reactions.append(original_reaction)
        print()
            
        joined_indexes = '-'.join([str(i) for i in indexes])
        cti_rxn.comment = "Reaction {:10s} has been replaced with AutoTST 2.0  #".format(joined_indexes)
        header = ["#########################################################",
                  "##  Reaction {:10s} has been replaced with AutoTST 2.0  ##".format(joined_indexes),
                  "##  Rxn String: {:43s} ##".format(rxn_string),
                  "#########################################################"]
            
        modified_reactions.insert(0, cti_rxn)
        parser.reactions = modified_reactions
        parser.writeCTI(
            header=header, 
            outName=os.path.join(
                "..", "alternatives", name, f"{name}.{atst_index}.{joined_indexes}.cti"
            ))

        parser.reactions = original_reactions
        
    parser.reactions = original_reactions
    

167 ch2(s) + h2 <=> ch3 + h

128 ch4 + h <=> ch3 + h2

2 oh + h2 <=> h + h2o

337 c2h3 + h <=> h2cc + h2

200 c2h4 + h (+ M) <=> c2h5 (+ M)

298 c2h4 + h <=> c2h3 + h2

132 ch4 + ch2 <=> ch3 + ch3

91 ch3o (+ M) <=> ch2o + h (+ M)

98 ch2o + h (+ M) <=> ch2oh (+ M)

190 c2h6 + h <=> c2h5 + h2

130 ch4 + o <=> ch3 + oh

133 ch3 + oh (+ M) <=> ch2(s) + h2o (+ M)

129 ch4 + oh <=> ch3 + h2o

117 ch3oh + h <=> ch2oh + h2

118 ch3oh + h <=> ch3o + h2

21 h2o2 + h <=> h2 + ho2

592 c3h5-a <=> c3h5-t

593 c3h5-a <=> c3h5-s

607 c3h5-t <=> c3h5-s

600 c3h4-p + h <=> c3h5-t

599 c3h4-a + h <=> c3h5-t

575 c3h4-a + h <=> c3h5-a

634 c3h4-p + h <=> c3h3 + h2

632 c3h4-p + h <=> c3h5-s

280 ch2co + h <=> hcco + h2

279 ch3co (+ M) <=> ch2co + h (+ M)

533 h + c3h6 <=> nc3h7

532 ch3 + c2h4 <=> nc3h7

526 h + c3h6 <=> ic3h7

554 c3h6 + h <=> c3h5-a + h2

555 c3h6 + h <=> c3h5-s + h2

556 c3h6 + h <=> c3h5-t + h2

320 c2h4 + ch3 <=> c2h3 + ch4

199 ch2(s) + c2h6 <=> ch3 + c2h5

442 ch3och2 <=> ch2o 

1890 c4h7oh2-2 + h <=> sc4h8oh-2

1874 ic3h6choh + h <=> ic4h8oh-1

1155 c2h5coch3 + h <=> c2h5coch2 + h2

1640 c4h7oh1-2 + h <=> c4h6oh1-32 + h2

1607 c4h7oh2-1 + h <=> c4h8oh-3

1406 ic3h7cho + h <=> ic3h7co + h2

508 c2h5 + c3h8 <=> c2h6 + ic3h7

509 c2h5 + c3h8 <=> c2h6 + nc3h7

779 c4h10 + ch3 <=> sc4h9 + ch4

1227 ic4h10 + ch3 <=> ic4h9 + ch4

1226 ic4h10 + ch3 <=> tc4h9 + ch4

778 c4h10 + ch3 <=> pc4h9 + ch4

393 ch3coch3 + o <=> ch3coch2 + oh

1235 ic4h10 + o <=> ic4h9 + oh

1234 ic4h10 + o <=> tc4h9 + oh

785 c4h10 + o <=> sc4h9 + oh

784 c4h10 + o <=> pc4h9 + oh

277 ho2ch2co <=> ch2co + ho2

460 och2ocho <=> hoch2oco

462 ch2oh + co2 <=> hoch2oco

274 o2ch2cho <=> ho2ch2co

2064 hoc2h4cho + h <=> hoc2h4co + h2

478 ch3ocho + ch3 <=> ch3oco + ch4

479 ch3ocho + ch3 <=> ch2ocho + ch4

444 ch3och2 + ch2o <=> ch3och3 + hco

240 c2h4o1-2 + ch3o <=> c2h3o1-2 + ch3oh

1524 c3h5oh + oh <=> ch2cch2oh + h2o

726 c3h6 + ho2 <=> c3h6ooh2-1

2058 hoch2cho + ch3 <=> hoch2co + ch4

725 c3h

772 c4h10 + c3h5-a <=> pc4h9 + c3h6

773 c4h10 + c3h5-a <=> sc4h9 + c3h6

1498 tc3h6cho + ch2o <=> ic3h7cho + hco

1469 ic4h6oh + ch2o <=> ic4h7oh + hco

1497 ic4h7oh + hco <=> ic4h7o + ch2o

536 c2h5cho + ic3h7 <=> c2h5co + c3h8

535 c2h5cho + nc3h7 <=> c2h5co + c3h8

1173 c2h5coch3 + c2h5 <=> c2h5coch2 + c2h6

1172 c2h5coch3 + c2h5 <=> ch3chcoch3 + c2h6

1171 c2h5coch3 + c2h5 <=> ch2ch2coch3 + c2h6

325 c2h4 + ch3co3 <=> c2h3 + ch3co3h

413 c2h3cho + ch3o2 <=> c2h3co + ch3o2h

1176 c2h3coch3 + ho2 <=> ch2choohcoch3

1481 ic3h5cho + ho2 <=> ic3h5co + h2o2

1210 sc3h5cho + ho2 <=> sc3h5co + h2o2

1509 ic3h5cho + ho2 <=> ic3h5o2hcho

1507 tc3h6o2cho <=> ic3h5o2hcho

1508 tc3h6o2cho <=> tc3h6o2hco

1175 ch3choococh3 <=> ch2choohcoch3

568 c3h6 + c2h5o2 <=> c3h5-a + c2h5o2h

1455 ic4h8 + ch3o2 <=> ic4h7 + ch3o2h

839 c4h8-1 + ch3o2 <=> c4h71-3 + ch3o2h

858 c4h8-2 + ch3o2 <=> c4h71-3 + ch3o2h

840 c4h8-1 + ch3o2 <=> c4h71-4 + ch3o2h

1164 c2h5coch3 + ch3o <=> c2h5coch2 + ch3oh

1188 nc3h7

1064 pc4h9o2 + ch2o <=> pc4h9o2h + hco

1326 ic4h9o2 + ch2o <=> ic4h9o2h + hco

673 nc3h7o2 + ch3cho <=> nc3h7o2h + ch3co

1327 tc4h9o2 + ch2o <=> tc4h9o2h + hco

1247 ic4h10 + o2cho <=> ic4h9 + ho2cho

795 c4h10 + o2cho <=> pc4h9 + ho2cho

796 c4h10 + o2cho <=> sc4h9 + ho2cho

1248 ic4h10 + o2cho <=> tc4h9 + ho2cho

1198 nc3h7cho + ch3o2 <=> c3h6cho-3 + ch3o2h

1167 c2h5coch3 + ch3o2 <=> c2h5coch2 + ch3o2h

1189 nc3h7cho + ch3o2 <=> nc3h7co + ch3o2h

1196 nc3h7cho + ch3o2 <=> c3h6cho-1 + ch3o2h

1197 nc3h7cho + ch3o2 <=> c3h6cho-2 + ch3o2h

1166 c2h5coch3 + ch3o2 <=> ch3chcoch3 + ch3o2h

1645 c4h7oh1-2 + ch3o2 <=> c4h6oh1-32 + ch3o2h

1639 c4h7oh2-2 + ch3o2 <=> c4h6oh1-32 + ch3o2h

1409 ic3h7cho + ch3o2 <=> ic3h6cho + ch3o2h

1651 c4h7oh1-1 + ch3o2 <=> c4h6oh1-13 + ch3o2h

518 nc3h7o2 + c3h8 <=> nc3h7o2h + nc3h7

519 nc3h7o2 + c3h8 <=> nc3h7o2h + ic3h7

520 ic3h7o2 + c3h8 <=> ic3h7o2h + nc3h7

521 ic3h7o2 + c3h8 <=> ic3h7o2h + ic3h7

1254 ic4h10 + c2h5o2 <=> tc4h9 + c2h5o2h

799 c2h5o

1037 C3H4-P + CH3 -> C3H3 + CH4
1038 C3H3 + CH4 -> C3H4-P + CH3

1007 C3H4-A + CH3 -> C3H3 + CH4
1008 C3H3 + CH4 -> C3H4-A + CH3

1452 C4H71-2 -> C3H4-A + CH3
1453 C3H4-A + CH3 -> C4H71-2

1456 C4H72-2 -> C3H4-P + CH3
1457 C3H4-P + CH3 -> C4H72-2

1454 C4H71-4 -> C2H4 + C2H3
1455 C2H4 + C2H3 -> C4H71-4

2312 IC4H7 -> C3H4-A + CH3
2313 C3H4-A + CH3 -> IC4H7

1458 C4H71-3 -> C4H6 + H
1459 C4H6 + H -> C4H71-3

1033 C3H4-P + O -> C3H3 + OH
1034 C3H3 + OH -> C3H4-P + O

1023 C3H4-P + OH -> C3H3 + H2O
1024 C3H3 + H2O -> C3H4-P + OH

999 C3H4-A + OH -> C3H3 + H2O
1000 C3H3 + H2O -> C3H4-A + OH

2454 CH2CCH2OH -> C3H4-A + OH
2455 C3H4-A + OH -> CH2CCH2OH

1220 C3H5O -> C2H3 + CH2O
1221 C2H3 + CH2O -> C3H5O

591 CH3COCH2 -> CH2CO + CH3
592 CH2CO + CH3 -> CH3COCH2

1785 CH2CH2CHO -> C2H4 + HCO
1786 C2H4 + HCO -> CH2CH2CHO

1218 C3H5O -> C2H3CHO + H
1219 C2H3CHO + H -> C3H5O

913 C3H6 + CH3 -> C3H5-S + CH4
914 C3H5-S + CH4 -> C3H6 + CH3

915 C3H6 + CH3 -> C3H5-T + CH4
916 C3H5-T + CH4 -> C3H6 + C

...

2007 SC4H9O2 + IC4H8 -> SC4H9O2H + IC4H7
2008 SC4H9O2H + IC4H7 -> SC4H9O2 + IC4H8

595 CH3COCH3 + CH3COCH2O2 -> CH3COCH2 + CH3COCH2O2H
596 CH3COCH2 + CH3COCH2O2H -> CH3COCH3 + CH3COCH2O2

2055 TC4H9O2 + C2H5CHO -> TC4H9O2H + C2H5CO
2056 TC4H9O2H + C2H5CO -> TC4H9O2 + C2H5CHO

1562 PC4H9O2 + C2H5CHO -> PC4H9O2H + C2H5CO
1563 PC4H9O2H + C2H5CO -> PC4H9O2 + C2H5CHO

2053 IC4H9O2 + C2H5CHO -> IC4H9O2H + C2H5CO
2054 IC4H9O2H + C2H5CO -> IC4H9O2 + C2H5CHO

1919 IC4H10 + SC4H9O2 -> IC4H9 + SC4H9O2H
1920 IC4H9 + SC4H9O2H -> IC4H10 + SC4H9O2

1913 IC4H10 + TC4H9O2 -> IC4H9 + TC4H9O2H
1914 IC4H9 + TC4H9O2H -> IC4H10 + TC4H9O2

1911 IC4H10 + IC4H9O2 -> IC4H9 + IC4H9O2H
1912 IC4H9 + IC4H9O2H -> IC4H10 + IC4H9O2

1334 SC4H9O2 + C4H10 -> SC4H9O2H + PC4H9
1335 SC4H9O2H + PC4H9 -> SC4H9O2 + C4H10

1921 IC4H10 + SC4H9O2 -> TC4H9 + SC4H9O2H
1922 TC4H9 + SC4H9O2H -> IC4H10 + SC4H9O2

1925 IC4H10 + PC4H9O2 -> TC4H9 + PC4H9O2H
1926 TC4H9 + PC4H9O2H -> IC4H10 + PC4H9O2

1989 TC4H9O2 + C4H10 -> TC4H9O2H + PC

740 ch3ocho + h -> ch3oco + h2
741 ch3oco + h2 -> ch3ocho + h

113 ch2o + ch3o -> ch3oh + hco
114 ch3oh + hco -> ch2o + ch3o

361 c2h4o1-2 + oh -> c2h3o1-2 + h2o
362 c2h3o1-2 + h2o -> c2h4o1-2 + oh

787 c3h8 + oh -> ic3h7 + h2o
788 ic3h7 + h2o -> c3h8 + oh

785 c3h8 + oh -> nc3h7 + h2o
786 nc3h7 + h2o -> c3h8 + oh

663 ch3och3 + ch3 -> ch3och2 + ch4
664 ch3och2 + ch4 -> ch3och3 + ch3

551 c2h5oh + ch3 -> pc2h4oh + ch4
552 pc2h4oh + ch4 -> c2h5oh + ch3

553 c2h5oh + ch3 -> sc2h4oh + ch4
554 sc2h4oh + ch4 -> c2h5oh + ch3

555 c2h5oh + ch3 -> c2h5o + ch4
556 c2h5o + ch4 -> c2h5oh + ch3

288 c2h6 + ch3o -> c2h5 + ch3oh
289 c2h5 + ch3oh -> c2h6 + ch3o

657 ch3och3 + o -> ch3och2 + oh
658 ch3och2 + oh -> ch3och3 + o

545 c2h5oh + o -> pc2h4oh + oh
546 pc2h4oh + oh -> c2h5oh + o

549 c2h5oh + o -> c2h5o + oh
550 c2h5o + oh -> c2h5oh + o

85 ch2o + ho2 -> hco + h2o2
86 hco + h2o2 -> ch2o + ho2

297 h2 + c2h5o2 -> h + c2h5o2h
298 h + c2h5o2h -> h2 + c2h5o2

210 ch4 + ch3o2 -> ch3 + ch3o2h
211 c

648 c2h5cho + c2h3 -> c2h5co + c2h4
649 c2h5co + c2h4 -> c2h5cho + c2h3

1844 sc3h5cho + ch3 -> sc3h5co + ch4
1845 sc3h5co + ch4 -> sc3h5cho + ch3

2348 ic3h5cho + ch3 -> ic3h5co + ch4
2349 ic3h5co + ch4 -> ic3h5cho + ch3

809 c3h8 + c3h5-a -> ic3h7 + c3h6
810 ic3h7 + c3h6 -> c3h8 + c3h5-a

807 c3h8 + c3h5-a -> nc3h7 + c3h6
808 nc3h7 + c3h6 -> c3h8 + c3h5-a

1259 c4h10 + c2h3 -> sc4h9 + c2h4
1260 sc4h9 + c2h4 -> c4h10 + c2h3

1257 c4h10 + c2h3 -> pc4h9 + c2h4
1258 pc4h9 + c2h4 -> c4h10 + c2h3

1846 sc3h5cho + o -> sc3h5co + oh
1847 sc3h5co + oh -> sc3h5cho + o

616 c2h3cho + ch3o -> c2h3co + ch3oh
617 c2h3co + ch3oh -> c2h3cho + ch3o

2360 tc3h6ocho -> ch3coch3 + hco
2361 ch3coch3 + hco -> tc3h6ocho

638 c2h5cho + c2h5 -> c2h5co + c2h6
639 c2h5co + c2h6 -> c2h5cho + c2h5

1385 c4h8-1 + ch3o -> c4h71-4 + ch3oh
1386 c4h71-4 + ch3oh -> c4h8-1 + ch3o

1383 c4h8-1 + ch3o -> c4h71-3 + ch3oh
1384 c4h71-3 + ch3oh -> c4h8-1 + ch3o

1418 c4h8-2 + ch3o -> c4h71-3 + ch3oh
1419 c4h71-3 + ch3oh -> c

2295 ic4h8 + ch3o2 -> ic4h7 + ch3o2h
2296 ic4h7 + ch3o2h -> ic4h8 + ch3o2

1379 c4h8-1 + ch3o2 -> c4h71-3 + ch3o2h
1380 c4h71-3 + ch3o2h -> c4h8-1 + ch3o2

1416 c4h8-2 + ch3o2 -> c4h71-3 + ch3o2h
1417 c4h71-3 + ch3o2h -> c4h8-2 + ch3o2

1381 c4h8-1 + ch3o2 -> c4h71-4 + ch3o2h
1382 c4h71-4 + ch3o2h -> c4h8-1 + ch3o2

1753 c2h5coch3 + ch3o -> c2h5coch2 + ch3oh
1754 c2h5coch2 + ch3oh -> c2h5coch3 + ch3o

1801 nc3h7cho + ch3o -> nc3h7co + ch3oh
1802 nc3h7co + ch3oh -> nc3h7cho + ch3o

1751 c2h5coch3 + ch3o -> ch3chcoch3 + ch3oh
1752 ch3chcoch3 + ch3oh -> c2h5coch3 + ch3o

1749 c2h5coch3 + ch3o -> ch2ch2coch3 + ch3oh
1750 ch2ch2coch3 + ch3oh -> c2h5coch3 + ch3o

1285 c4h10 + c2h5o -> pc4h9 + c2h5oh
1286 pc4h9 + c2h5oh -> c4h10 + c2h5o

1287 c4h10 + c2h5o -> sc4h9 + c2h5oh
1288 sc4h9 + c2h5oh -> c4h10 + c2h5o

2412 tc3h6cho + ho2 -> ic3h7cho + o2
2413 ic3h7cho + o2 -> tc3h6cho + ho2

416 ch2o + ch3co3 -> hco + ch3co3h
417 hco + ch3co3h -> ch2o + ch3co3

2328 ic4h7oh + ho2 -> ic4h6oh + h2o2
2

669 ch3och3 + ch3och2o2 -> ch3och2 + ch3och2o2h
670 ch3och2 + ch3och2o2h -> ch3och3 + ch3och2o2

2055 ic4h9o2 + h2o2 -> ic4h9o2h + ho2
2056 ic4h9o2h + ho2 -> ic4h9o2 + h2o2

1604 h2o2 + pc4h9o2 -> ho2 + pc4h9o2h
1605 ho2 + pc4h9o2h -> h2o2 + pc4h9o2

2426 ic4h7o + ic4h8 -> ic4h7oh + ic4h7
2427 ic4h7oh + ic4h7 -> ic4h7o + ic4h8

2324 ic4h6oh + ic4h8 -> ic4h7oh + ic4h7
2325 ic4h7oh + ic4h7 -> ic4h6oh + ic4h8

2382 tc3h6cho + ic4h8 -> ic3h7cho + ic4h7
2383 ic3h7cho + ic4h7 -> tc3h6cho + ic4h8

1099 c2h3cho + ic3h7o2 -> c2h3co + ic3h7o2h
1100 c2h3co + ic3h7o2h -> c2h3cho + ic3h7o2

1097 c2h3cho + nc3h7o2 -> c2h3co + nc3h7o2h
1098 c2h3co + nc3h7o2h -> c2h3cho + nc3h7o2

1387 c4h8-1 + ch3co3 -> c4h71-3 + ch3co3h
1388 c4h71-3 + ch3co3h -> c4h8-1 + ch3co3

2005 nc3h7o2 + ic4h8 -> nc3h7o2h + ic4h7
2006 nc3h7o2h + ic4h7 -> nc3h7o2 + ic4h8

1993 tc4h9o2 + c3h6 -> tc4h9o2h + c3h5-a
1994 tc4h9o2h + c3h5-a -> tc4h9o2 + c3h6

1395 c4h8-1 + nc3h7o2 -> c4h71-3 + nc3h7o2h
1396 c4h71-3 + nc3h7o2h -> c4h8

# Some sanity checks to make sure that we're making the right number of files. 

`-1` is to subtract out the `master.cti` file

In [14]:
print(df.heptane_cti_str.dropna().shape[0] == (len(os.listdir('../alternatives/heptane/'))) -1)
df.heptane_cti_str.dropna().shape[0], len(os.listdir('../alternatives/heptane/'))

True


(536, 537)

In [15]:
print(df.methylheptane_cti_str.dropna().shape[0] == (len(os.listdir('../alternatives/methylheptane/'))) -1)
df.methylheptane_cti_str.dropna().shape[0], len(os.listdir('../alternatives/methylheptane/'))

True


(539, 540)

In [16]:
print(df.butanol_cti_str.dropna().shape[0] == (len(os.listdir('../alternatives/butanol/'))) -1)
df.butanol_cti_str.dropna().shape[0], len(os.listdir('../alternatives/butanol/'))

True


(832, 833)

# Writing the species dictionary files

In [17]:
species_strings = {'butanol': """{}: 
    O2: "o2" 
    N2: "n2" 
    Ar: "ar" 
    He: "he" 
    CO2: "co2" 
    H2O: "h2o" 
    n-butanol: "nc4h9oh" 
    
""",
'heptane':"""{}: 
    O2: "O2" 
    N2: "N2" 
    Ar: "AR" 
    He: "HE" 
    CO2: "CO2" 
    H2O: "H2O" 
    nC7H16: "NC7H16"
    
""",

'methylheptane':"""{}:
    O2: "o2"
    N2: "n2"
    Ar: "ar"
    He: "he"
    CO2: "co2"
    H2O: "h2o"
    3-methyl-heptane: "c8h18-3"
    
"""}

In [18]:
for name in parsers.keys():
    strings = '---\n'
    
    files = sorted(os.listdir(f'../alternatives/{name}'))
    base_string = species_strings[name]
    
    for fi in files:
        strings += base_string.format(fi)
        
    with open(f'../run-pyteck/{name}-species.txt', 'w') as f:
        f.write(strings)
        